# NB02: Query & Explore Large Scale Tables

If you’ve ever tried visualizing vast geospatial datasets—such as billions of points—you’ve likely run into performance bottlenecks or high costs. S&P Global Commodity Insights set out to solve a major challenge on Databricks:

> __Efficiently rendering geospatial content while scaling performance and reducing costs.__ 

Traditional approaches often rely on external geospatial databases or specialized ETL pipelines, forcing data copies and limiting flexibility. In this notebook, we explore our H3 indexing strategy which overcomes these challenges from a single-source-of-truth.


__Notes:__

* Friendly for use in Serverless compute on Databricks
* Uses Databricks built-in types and [ST Geospatial Functions](https://docs.databricks.com/aws/en/sql/language-manual/sql-ref-st-geospatial-functions), available in public preview since DBR 17.1
* Uses Databricks [H3 Geospatial Functions](https://docs.databricks.com/aws/en/sql/language-manual/sql-ref-h3-geospatial-functions), which have been GA since DBR 11.x

---
__Authors:__
- Hubert Boguski <hubert.boguski@spglobal.com>
- Jeff Jaco <jeff.jaco@spglobal.com>
- Debaprasad Satapathy <debaprasad.satapathy@spglobal.com>
- Michael Johns <mjohns@databricks.com>

In [0]:
%sql
-- uncomment to list all available st_ or h3_ expressions
-- SHOW FUNCTIONS LIKE "ST_*";
-- SHOW FUNCTIONS LIKE "H3_*";

## [1] Setup

In [0]:
%pip install keplergl==0.3.2 --quiet

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
catalog_name = 'mjohns'            # <- set to nb01 value
schema_name = 'liquid_nyc_h3_trip' # <- set to nb01 value
spark.catalog.setCurrentCatalog(catalog_name)
spark.catalog.setCurrentDatabase(schema_name)

In [0]:
from keplergl import KeplerGl
import os


> We are using kepler.gl initially within the notebook (vs app).

__Note:__

 Displaying too many records with kepler.gl in different notebook cells may crash this session. Therefore, there is a default 40,000 records **limit_amount** filter for every visualize_with_kepler function call to prevent the session from crashing. If you wish to see more records in any one visualize_with_kepler call, simply add a higher limit_amount, e.g. - visualize_with_kepler(dataframes, wkt_viewport, zoom_level, include_map_extent=False, limit_amount=**your_higher_amount**)

In [0]:
# run this cell for viz helpers
kepler_height = 800
kepler_width = 1200

def display_kepler_map(kmap: KeplerGl, height=kepler_height, width=kepler_width) -> None:
    """
    Renders a Kepler.gl map with specified dimensions.
    """
    displayHTML(
        kmap
        ._repr_html_()
        .decode("utf-8")
        .replace(".height||400", f".height||{height}")
        .replace(".width||400", f".width||{width}")
    )

def prepare_data_layers(dataframes, bbox_layer=None, limit_amount=40_000):
    """
    Converts Spark DataFrame(s) to Pandas and organizes them into layers for Kepler.gl.
    Accepts either a single DataFrame or a list of DataFrames. Optionally accepts a bbox_layer.
    """
    data_layers = {}
    
    if not isinstance(dataframes, list):
        dataframes = [dataframes]

    for i, df in enumerate(dataframes):
        layer_name = f'layer_{i+1}'
        data_layers[layer_name] = df.limit(limit_amount).toPandas()
    
    if bbox_layer is not None:
        data_layers['bbox_layer'] = bbox_layer.toPandas()

    return data_layers

def visualize_with_kepler(dataframes, wkt_viewport, zoom_level, include_map_extent=False, limit_amount=40_000):
    """
    Prepares and displays a Kepler.gl map with the provided DataFrame(s).
    """
    bbox_df = None
    if include_map_extent:
        bbox_df = spark.sql(f"SELECT '{wkt_viewport}' AS wkt_viewport")
    
    layers = prepare_data_layers(dataframes, bbox_layer=bbox_df, limit_amount=limit_amount)
    
    spark.sql(f"CREATE OR REPLACE TEMP VIEW polygon_view AS SELECT '{wkt_viewport}' AS polygon")
        
    viewport_df = spark.sql("""
    SELECT 
        ST_X(ST_Centroid(ST_GeomFromText(polygon))) as xcentroid, 
        ST_Y(ST_Centroid(ST_GeomFromText(polygon))) as ycentroid
    FROM polygon_view
    """).collect()[0]

    kepler_map = KeplerGl(
        config={
            'version': 'v1',
            'mapState': {
                'latitude': viewport_df.ycentroid,
                'longitude': viewport_df.xcentroid,
                'zoom': zoom_level
            },
            'mapStyle': {'styleType': 'dark'},
            'options': {'readOnly': False, 'centerMap': True}
        },
        data=layers,
    )

    display_kepler_map(kepler_map)

print("::: Viz Helpers :::")
print("- display_kepler_map(kmap: KeplerGl, height=kepler_height, width=kepler_width) -> None")
print("- prepare_data_layers(dataframes, bbox_layer=None, limit_amount=40_000)")
print("- visualize_with_kepler(dataframes, wkt_viewport, zoom_level, include_map_extent=False, limit_amount=40_000)")

::: Viz Helpers :::
- display_kepler_map(kmap: KeplerGl, height=kepler_height, width=kepler_width) -> None
- prepare_data_layers(dataframes, bbox_layer=None, limit_amount=40_000)
- visualize_with_kepler(dataframes, wkt_viewport, zoom_level, include_map_extent=False, limit_amount=40_000)


## [2] Initial Analysis: `taxi_trips` Table

> This analytic is derived from the base table generated in the first notebook.

In [0]:
%sql 
SELECT * FROM taxi_trips LIMIT 10;

geohash_pickup geohash_dropoff travel_time_minutes pickup_hour pickup_day pickup_month pickup_year dropoff_hour dropoff_day dropoff_month dropoff_year total_amount pickup_datetime dropoff_datetime trip_distance passenger_count payment_type fare_amount extra mta_tax tip_amount tolls_amount geom_pickup geom_dropoff pickup_longitude pickup_latitude dropoff_longitude dropoff_latitude dr5ru0w8kvx2 dr5rsrtwd5hq 3.616667 17 3 1 2016 17 3 1 2016 6.35 2016-01-03T17:14:49Z 2016-01-03T17:18:26Z 0.7 1 1 4.5 0.0 0.5 1.05 0.0 SRID=4326;POINT(-73.99476623535156 40.7401237487793) SRID=4326;POINT(-73.98527526855469 40.73569107055664) -73.99476623535156 40.7401237487793 -73.98527526855469 40.73569107055664 dr5rudewgn8d dr5rsq9juv1s 10.483333 17 3 1 2016 17 3 1 2016 9.8 2016-01-03T17:24:14Z 2016-01-03T17:34:43Z 1.91 1 2 9.0 0.0 0.5 0.0 0.0 SRID=4326;POINT(-73.97699737548828 40.75223159790039) SRID=4326;POINT(-73.99134063720703 40.730079650878906) -73.97699737548828 40.75223159790039 -73.99134063720703 40.730079650878906 dr5ru960vewp dr5rsrh9mzes 4.750000 17 3 1 2016 17 3 1 2016 7.3 2016-01-03T17:30:47Z 2016-01-03T17:35:32Z 1.0 1 1 5.5 0.0 0.5 1.0 0.0 SRID=4326;POINT(-73.97894287109375 40.744319915771484) SRID=4326;POINT(-73.98648834228516 40.7320671081543) -73.97894287109375 40.744319915771484 -73.98648834228516 40.7320671081543 dr5ru7tb4ven dr5ru1x9gqs4 7.900000 17 3 1 2016 17 3 1 2016 9.36 2016-01-03T17:39:41Z 2016-01-03T17:47:35Z 0.98 1 1 7.0 0.0 0.5 1.56 0.0 SRID=4326;POINT(-73.98490142822266 40.756561279296875) SRID=4326;POINT(-73.99346160888672 40.745880126953125) -73.98490142822266 40.756561279296875 -73.99346160888672 40.745880126953125 dr5ru1ft3f8v dr5rsq8f421b 13.500000 18 3 1 2016 18 3 1 2016 13.55 2016-01-03T18:00:11Z 2016-01-03T18:13:41Z 2.1 1 1 10.5 0.0 0.5 2.25 0.0 SRID=4326;POINT(-74.00039672851562 40.747833251953125) SRID=4326;POINT(-73.99179077148438 40.729408264160156) -74.00039672851562 40.747833251953125 -73.99179077148438 40.729408264160156 dr5ru1jdefmp dr5rspnxwjr4 4.600000 18 3 1 2016 18 3 1 2016 7.56 2016-01-03T18:09:36Z 2016-01-03T18:14:12Z 1.03 1 1 5.5 0.0 0.5 1.26 0.0 SRID=4326;POINT(-73.99618530273438 40.74324035644531) SRID=4326;POINT(-73.99471282958984 40.73312759399414) -73.99618530273438 40.74324035644531 -73.99471282958984 40.73312759399414 dr5ru85jz1ee dr5rsrvfrxss 30.833333 18 3 1 2016 18 3 1 2016 30.35 2016-01-03T18:12:08Z 2016-01-03T18:42:58Z 6.7 1 1 24.5 0.0 0.5 5.05 0.0 SRID=4326;POINT(-73.97750854492188 40.73830032348633) SRID=4326;POINT(-73.98469543457031 40.736358642578125) -73.97750854492188 40.73830032348633 -73.98469543457031 40.736358642578125 dr5rud5rz631 dr5rsqm32891 9.666667 18 3 1 2016 18 3 1 2016 11.75 2016-01-03T18:30:22Z 2016-01-03T18:40:02Z 1.8 1 1 9.0 0.0 0.5 1.95 0.0 SRID=4326;POINT(-73.97715759277344 40.7496337890625) SRID=4326;POINT(-73.98568725585938 40.727909088134766) -73.97715759277344 40.7496337890625 -73.98568725585938 40.727909088134766 dr5rte89v8yh dr5rt0swr3cn 12.266667 18 3 1 2016 19 3 1 2016 12.96 2016-01-03T18:51:42Z 2016-01-03T19:03:58Z 1.95 1 1 10.0 0.0 0.5 2.16 0.0 SRID=4326;POINT(-73.93705749511719 40.712890625) SRID=4326;POINT(-73.9534683227539 40.69718933105469) -73.93705749511719 40.712890625 -73.9534683227539 40.69718933105469 dr5ru9936tt2 dr5rsrpb5x1g 4.816667 18 3 1 2016 19 3 1 2016 7.8 2016-01-03T18:59:41Z 2016-01-03T19:04:30Z 1.3 1 1 6.0 0.0 0.5 1.0 0.0 SRID=4326;POINT(-73.9801025390625 40.74578857421875) SRID=4326;POINT(-73.98212432861328 40.731849670410156) -73.9801025390625 40.74578857421875 -73.98212432861328 40.731849670410156

In [0]:
%sql
SELECT format_number(count(*), 0) AS count FROM taxi_trips;

count 33,921,861

### Optimizing the Map Extent

> When using just the base table, a query from our client / app might look something like the following.

__Tips:__

Once the Map is rendered with Keplergl...
  * You can adjust color, size, opacity, etc
  * You can select the layer panel and unhide the dropoff layer to view it
  * Bonus: you can also unhide the Arc Layer after rendering

#### Pickups Intersecting Map Extent

> Specify map extent polygon. __Note:__ You could include dropoffs as well (not shown). _This initial example is done on a smaller map extent._

In [0]:
%sql
-- Query sent to Databricks Serverless SQL Warehouse using Databricks Spatial SQL

CREATE OR REPLACE TEMPORARY VIEW sp_point_v AS (
  WITH map_extent AS (
  SELECT 
    st_geomfromwkt('POLYGON ((-74.023905 40.700032, -74.023905 40.717794, -73.987169 40.717794, -73.987169 40.700032, -74.023905 40.700032))', 4326) AS sp_office
  )

  SELECT 
    pickup_longitude, 
    pickup_latitude --, 
    
    -- Optionally query additional points/attributes
    -- dropoff_longitude,
    -- dropoff_latitude,
    -- trip_cost,
    -- ...
  FROM 
    taxi_trips, 
    map_extent
  WHERE ST_INTERSECTS(sp_office, geom_pickup)
);

In [0]:
map_extent = 'POLYGON ((-74.023905 40.700032, -74.023905 40.717794, -73.987169 40.717794, -73.987169 40.700032, -74.023905 40.700032))'
map_zoom = 14.1
map_extent_sp_df = spark.sql("""
SELECT pickup_longitude, pickup_latitude
FROM sp_point_v 
""")

In [0]:
print("...data queried (showing map extent bounding box):")
visualize_with_kepler(
  dataframes=map_extent_sp_df,
  wkt_viewport=map_extent,
  zoom_level=map_zoom,
  include_map_extent=True
)

...data queried (showing map extent bounding box):
User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


<!doctype html> Kepler.gl

In [0]:
print("...user view (without map extent bounding box)")
visualize_with_kepler(
  dataframes=map_extent_sp_df,
  wkt_viewport=map_extent,
  zoom_level=map_zoom,
  include_map_extent=False
)

...user view (without map extent bounding box)
User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


<!doctype html> Kepler.gl

#### Issue with Larger Map Extent @ Massive Scale Data

> When we zoom out and try to bring in more data, we start to hit some issues visualizing with just the base table. __Most notably, our data is larger than what we can reasonably return directly for a larger viewport, without some sort of simplification / aggregation.__

* More points were included within the map extent.
* Points were likely to be farther from each other and therefore in different partitions, resulting in more files needed to be read.
* Rendering more points on the client became computationally expensive.

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW larger_point_v AS (
  WITH map_extent AS (
  SELECT 
    st_geomfromwkt('POLYGON ((-74.091797 40.663973, -74.091797 40.759741, -73.905029 40.759741, -73.905029 40.663973, -74.091797 40.663973))', 4326) AS larger_map_extent
  )

  SELECT 
    pickup_longitude, 
    pickup_latitude
  FROM 
    taxi_trips, 
    map_extent
  WHERE 
  ST_INTERSECTS(larger_map_extent, geom_pickup)
);

##### Even after bumping up the limit amount to 80K, we still have a lot of "raw" events clustered within the downtown area, so we never render the other events. For massive scale data, we need to approach this differently.

In [0]:
larger_map_extent_df = spark.sql("""
SELECT pickup_longitude, pickup_latitude
FROM larger_point_v 
""")

print("...data queried (showing map extent bounding box):")
visualize_with_kepler(
  dataframes=larger_map_extent_df,
  wkt_viewport='POLYGON ((-74.091797 40.663973, -74.091797 40.759741, -73.905029 40.759741, -73.905029 40.663973, -74.091797 40.663973))',
  zoom_level=11.7,
  include_map_extent=True,
  limit_amount=80_000
)

...data queried (showing map extent bounding box):
User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


<!doctype html> Kepler.gl

## [3] Initial Aggregated H3 Analysis: `h3_taxi_trips` Table

> This analytic is derived from the h3 table generated in the first notebook.

By way of introduction, here is a simple example of the way the h3 cellid hierarchy works. __Note:__ We are using all even resolutions to avoid the back and forth rotation effects when mixing even and odd.

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW hierachy_cell_v AS (
  SELECT 
  -74.008809 AS lon,
  40.703351 AS lat,
  h3_longlatash3string(lon, lat, 8) AS cell_8,
  h3_longlatash3string(lon, lat, 10) AS cell_10,
  h3_longlatash3string(lon, lat, 12) AS cell_12
);

SELECT lon, lat, cell_8, cell_10, cell_12 FROM hierachy_cell_v;

lon lat cell_8 cell_10 cell_12 -74.008809 40.703351 882a10728bfffff 8a2a10728b9ffff 8c2a10728b9b9ff

In [0]:
hierachy_cell_df = spark.sql("""
SELECT 
  CAST(lon AS FLOAT) AS lon, 
  CAST(lat AS FLOAT) AS lat,
  cell_12,
  cell_10,
  cell_8
FROM hierachy_cell_v 
""")

print("::: h3 cellid hierarchy for sample point :::")
visualize_with_kepler(
  dataframes=hierachy_cell_df,
  wkt_viewport='POLYGON ((-74.04871 40.687017, -74.04871 40.7189, -73.98056 40.7189, -73.98056 40.687017, -74.04871 40.687017))',
  zoom_level=15,
  include_map_extent=False
)

::: h3 cellid hierarchy for sample point :::
User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


<!doctype html> Kepler.gl

### Here is the `h3_taxi_trips` table

In [0]:
%sql 
SELECT * FROM h3_taxi_trips LIMIT 10;

pickup_cell_12 pickup_cell_10 pickup_cell_8 dropoff_cell_12 dropoff_cell_10 dropoff_cell_8 geohash_pickup geohash_dropoff travel_time_minutes pickup_hour pickup_day pickup_month pickup_year dropoff_hour dropoff_day dropoff_month dropoff_year total_amount pickup_datetime dropoff_datetime trip_distance passenger_count payment_type fare_amount extra mta_tax tip_amount tolls_amount geom_pickup geom_dropoff pickup_longitude pickup_latitude dropoff_longitude dropoff_latitude 631243922693591551 622236723438878719 613229524185776127 631243922753140735 622236723498418175 613229524244496383 dr5ru3tjwnp1 dr5rumr63nzv 8.450000 11 9 1 2016 11 9 1 2016 10.55 2016-01-09T11:41:55Z 2016-01-09T11:50:22Z 1.8 1 1 8.0 0.0 0.5 1.75 0.0 SRID=4326;POINT(-73.98578643798828 40.74652099609375) SRID=4326;POINT(-73.98291015625 40.76656723022461) -73.98578643798828 40.74652099609375 -73.98291015625 40.76656723022461 631243922693229567 622236723438518271 613229524185776127 631243922747702783 622236723492978687 613229524240302079 dr5ru634nvty dr5rusq01bn8 23.350000 9 12 1 2016 9 12 1 2016 15.3 2016-01-12T09:16:17Z 2016-01-12T09:39:38Z 1.79 2 2 14.5 0.0 0.5 0.0 0.0 SRID=4326;POINT(-73.99124908447266 40.750038146972656) SRID=4326;POINT(-73.9736099243164 40.760650634765625) -73.99124908447266 40.750038146972656 -73.9736099243164 40.760650634765625 631243922693247999 622236723438518271 613229524185776127 631243922760641535 622236723505922047 613229524252884991 dr5ru636jdb7 dr5ruthfx3c0 9.300000 22 10 1 2016 22 10 1 2016 9.8 2016-01-10T22:04:50Z 2016-01-10T22:14:08Z 1.6 1 2 8.5 0.5 0.5 0.0 0.0 SRID=4326;POINT(-73.990966796875 40.750022888183594) SRID=4326;POINT(-73.97509765625 40.76520919799805) -73.990966796875 40.750022888183594 -73.97509765625 40.76520919799805 631243922681784319 622236723427049471 613229524173193215 631243922753539583 622236723498811391 613229524244496383 dr5ru3tbw7uv dr5rum7fubcs 12.933333 16 9 1 2016 17 9 1 2016 10.8 2016-01-09T16:54:24Z 2016-01-09T17:07:20Z 2.1 1 2 10.0 0.0 0.5 0.0 0.0 SRID=4326;POINT(-73.98474884033203 40.74565124511719) SRID=4326;POINT(-73.98756408691406 40.76662063598633) -73.98474884033203 40.74565124511719 -73.98756408691406 40.76662063598633 631243922694858751 622236723440123903 613229524185776127 631243922753129983 622236723498418175 613229524244496383 dr5ru4xhx8ke dr5rumrtvqdd 6.783333 22 9 1 2016 22 9 1 2016 9.95 2016-01-09T22:00:02Z 2016-01-09T22:06:49Z 1.3 2 1 7.0 0.5 0.5 1.65 0.0 SRID=4326;POINT(-73.99396514892578 40.75181198120117) SRID=4326;POINT(-73.98239135742188 40.76716613769531) -73.99396514892578 40.75181198120117 -73.98239135742188 40.76716613769531 631243922693233663 622236723438518271 613229524185776127 631243923160196607 622236723905462271 613229524651343871 dr5ru632e1n6 dr5x8rtbn4c7 25.366667 19 9 1 2016 20 9 1 2016 44.34 2016-01-09T19:40:55Z 2016-01-09T20:06:17Z 11.1 2 1 33.0 0.0 0.5 5.0 5.54 SRID=4326;POINT(-73.9910659790039 40.749755859375) SRID=4326;POINT(-73.8089828491211 40.73457336425781) -73.9910659790039 40.749755859375 -73.8089828491211 40.73457336425781 631243922682057727 622236723437076479 613229524183678975 631243922756386303 622236723501662207 613229524250787839 dr5ru88qefmp dr5ruuw469vq 10.350000 21 28 1 2016 21 28 1 2016 10.3 2016-01-28T21:36:33Z 2016-01-28T21:46:54Z 1.91 5 2 9.0 0.5 0.5 0.0 0.0 SRID=4326;POINT(-73.9814224243164 40.741180419921875) SRID=4326;POINT(-73.96259307861328 40.762420654296875) -73.9814224243164 40.741180419921875 -73.96259307861328 40.762420654296875 631243922694554111 622236723439828991 613229524185776127 631243923229082623 622236723974373375 613229524720549887 dr5ru6kmvhky dr5rvzwzzvf7 20.100000 4 16 1 2016 4 16 1 2016 21.3 2016-01-16T04:08:18Z 2016-01-16T04:28:24Z 5.84 1 2 20.0 0.5 0.5 0.0 0.0 SRID=4326;POINT(-73.98686218261719 40.750675201416016) SRID=4326;POINT(-73.91739654541016 40.77986526489258) -73.98686218261719 40.750675201416016 -73.91739654541016 40.77986526489258 631243922693599743 622236723438878719 613229524185776127 631243923239803903 62223

In [0]:
%sql
SELECT format_number(count(*), 0) AS count FROM h3_taxi_trips;

count 33,921,861

### Optimizing the Map Extent using H3

> We can take advantage of the H3 hierarchy in a few different ways.

  (a) Convert our search polygon from the map extent into an h3 covering set    
  (b) Aggregate our massive point data into counts per h3 cell resolution

#### (a) Convert our search polygon from the map extent into an h3 covering set 

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW h3_cover_cell_8_v AS (
  WITH map_extent AS (
  SELECT 
    'POLYGON ((-74.050598 40.699381, -74.050598 40.793279, -73.848724 40.793279, -73.848724 40.699381, -74.050598 40.699381))' AS bounding_box
  ),
  cells_in_view AS (
    SELECT 
      EXPLODE(h3_coverash3(bounding_box, 8)) AS h3_cell
    FROM 
      map_extent
  )
  SELECT 
    v.h3_cell
  FROM
    cells_in_view v
);

In [0]:
cell_covered_map_extent_df = spark.sql("""
SELECT h3_h3tostring(h3_cell) as cell_8
FROM h3_cover_cell_8_v 
""")

print("::: map extent with its h3 covering set at resolution 8 :::")
visualize_with_kepler(
  dataframes=cell_covered_map_extent_df,
  wkt_viewport='POLYGON ((-74.050598 40.699381, -74.050598 40.793279, -73.848724 40.793279, -73.848724 40.699381, -74.050598 40.699381))', 
  zoom_level=11.5, 
  include_map_extent=True
)

::: map extent with its h3 covering set at resolution 8 :::
User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


<!doctype html> Kepler.gl

#### (b) Aggregate our massive point data into counts per h3 cell resolution

> Aggregate pickups into larger hexagons when zoomed out and smaller hexagons when zoomed in. We are showing an example with h3 resolution 12, but this can be applied to any / multiple resolutions.

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW pickup_cell_12_v AS (
  WITH map_extent AS (
  SELECT 
    'POLYGON ((-73.885202 40.767737, -73.885202 40.780541, -73.854818 40.780541, -73.854818 40.767737, -73.885202 40.767737))' AS bounding_box
  ),
  cells_in_view AS (
    SELECT 
      EXPLODE(h3_coverash3(bounding_box, 12)) AS h3_cell
    FROM 
      map_extent
  ),
  aggregated_data AS (
    SELECT
      pickup_cell_12,
      AVG(travel_time_minutes) as avg_travel_time_minutes,
      COUNT(*) AS amount_of_pickups,
      SUM(total_amount) AS total_revenue
    FROM 
      h3_taxi_trips
    GROUP BY 
      pickup_cell_12
  )
  SELECT 
    a.pickup_cell_12,
    a.avg_travel_time_minutes,
    a.amount_of_pickups,
    a.total_revenue
  FROM 
    aggregated_data a
  JOIN 
    cells_in_view v
  ON 
    a.pickup_cell_12 = v.h3_cell
);

#### Pickups @ JFK?

> As in Iteration 1 with the base `taxi_trips` table (without h3), we are querying for pickups. If you chose to implement dropoff logic, you could easily look for dropoffs in JFK.

In [0]:
print("...jfk user view @ res 12")
visualize_with_kepler(
  dataframes=spark.sql("""
SELECT 
  h3_h3tostring(pickup_cell_12) as pickup_cell_12, -- converting to string, floats due to kepler limitations
  CAST(avg_travel_time_minutes AS FLOAT) as avg_travel_time_minutes,
  amount_of_pickups,
  CAST(total_revenue AS FLOAT) as total_revenue
FROM pickup_cell_12_v
"""),
  wkt_viewport='POLYGON ((-73.885202 40.767737, -73.885202 40.780541, -73.854818 40.780541, -73.854818 40.767737, -73.885202 40.767737))',
  zoom_level=15.05,
  include_map_extent=False
)

...jfk user view @ res 12
User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


<!doctype html> Kepler.gl

#### Rush to Flight [S&P Office to JFK]

In [0]:
%sql
-- We could also aggregate by dropoffs with short travel times to even better zones, but saved that to the next example
CREATE OR REPLACE TEMPORARY VIEW rush_to_flight_cell_12_v AS (
  WITH sp_map_extent AS ( -- Used for both current view map view and selection of taxi trips around S&P NYC Office, could have a third map extent for current map view if user zooms/pans around
  SELECT 
    st_geomfromwkt('POLYGON ((-74.019656 40.699902, -74.019656 40.706994, -74.00382 40.706994, -74.00382 40.699902, -74.019656 40.699902))', 4326) AS bounding_box
  ),
  jfk_map_extent AS (
    SELECT 
      st_geomfromwkt('POLYGON ((-73.887691 40.767477, -73.887691 40.78665, -73.853102 40.78665, -73.853102 40.767477, -73.887691 40.767477))', 4326) AS bounding_box
  ),
  cells_in_view AS ( 
    SELECT 
      EXPLODE(h3_coverash3(st_astext(bounding_box), 12)) AS h3_cell
    FROM 
      sp_map_extent
  ),
  aggregated_data AS (
    SELECT
      pickup_cell_12,
      pickup_month,
      AVG(travel_time_minutes) AS avg_travel_time_minutes
    FROM 
      h3_taxi_trips,    
      sp_map_extent as source,
      jfk_map_extent as destination
    WHERE
      ST_INTERSECTS(source.bounding_box, geom_pickup)
      AND ST_INTERSECTS(destination.bounding_box, geom_dropoff)
      AND pickup_day BETWEEN 20 AND 31 -- We can filter here too, but limit user interaction compared to the group by
      AND pickup_hour BETWEEN 7 AND 19 -- 7am to 7pm
      -- AND pickup_month = 12 -- We can filter here too, but would limit user interaction by having less records in the result set to analyze
    GROUP BY 
      pickup_cell_12, pickup_month
  )
  SELECT 
    a.pickup_cell_12,
    a.pickup_month,
    a.avg_travel_time_minutes
  FROM 
    aggregated_data a
  JOIN
    cells_in_view v
  ON 
    a.pickup_cell_12 = v.h3_cell
  ORDER BY
    a.pickup_month
);

SELECT COUNT(*) FROM rush_to_flight_cell_12_v; -- Sanity Check

count(1) 1381

In [0]:
rush_to_flight_cell_12_df = spark.sql("""
SELECT h3_h3tostring(pickup_cell_12) as pickup_cell_12,   
CASE 
    WHEN pickup_month = 1 THEN 'January'
    WHEN pickup_month = 2 THEN 'February'
    WHEN pickup_month = 3 THEN 'March'
    WHEN pickup_month = 4 THEN 'April'
    WHEN pickup_month = 5 THEN 'May'
    WHEN pickup_month = 6 THEN 'June'
    WHEN pickup_month = 7 THEN 'July'
    WHEN pickup_month = 8 THEN 'August'
    WHEN pickup_month = 9 THEN 'September'
    WHEN pickup_month = 10 THEN 'October'
    WHEN pickup_month = 11 THEN 'November'
    WHEN pickup_month = 12 THEN 'December'
END AS month,  
CAST(avg_travel_time_minutes AS FLOAT) AS avg_travel_time_minutes
FROM rush_to_flight_cell_12_v 
ORDER BY pickup_month DESC
""")

print("::: Rush to Flight :::")
visualize_with_kepler(
    dataframes=rush_to_flight_cell_12_df,
    wkt_viewport='POLYGON ((-74.019656 40.699902, -74.019656 40.706994, -74.00382 40.706994, -74.00382 40.699902, -74.019656 40.699902))',
    zoom_level=16,
    include_map_extent=False
)

::: Rush to Flight :::
User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


<!doctype html> Kepler.gl

## [4] Putting it all Together: Self-Service Map Analytics with H3

The number of records returned significantly influences the approach. Generally:

  - Grouping by an excessive number of columns can result in an overwhelming number of records. Therefore, it is advisable to minimize the number of grouping columns.
  - Lower cell resolutions aggregate more records, resulting in less records. This is particularly suitable for our focus on NYC and its surrounding areas, where a resolution of 8 is optimal. The example uses resolution 12 to showcase that by tuning these tradeoff, returning higher resolutions are possible. For spatial data covering larger areas, such as the entire USA, larger hexagons may be more appropriate.


In [0]:
%sql
-- Resolution 8 View
CREATE OR REPLACE TEMPORARY VIEW pickup_parent_cell_8_v AS (
  WITH map_extent AS (
  SELECT 
    st_geomfromwkt('POLYGON ((-74.050598 40.699381, -74.050598 40.793279, -73.848724 40.793279, -73.848724 40.699381, -74.050598 40.699381))', 4326) AS bounding_box
  ),
  cells_in_view AS (
    SELECT 
      EXPLODE(h3_coverash3(st_astext(bounding_box), 8)) AS h3_cell
    FROM 
      map_extent
  ),
  parent_cells AS (
    SELECT
      pickup_cell_8,
      total_amount
    FROM 
      h3_taxi_trips
  ),
  aggregated_data AS (
    SELECT
      pickup_cell_8,
      COUNT(*) AS amount_of_pickups,
      AVG(total_amount) AS avg_trip_cost
    FROM 
      parent_cells
    GROUP BY 
      pickup_cell_8
  )
  SELECT 
    a.pickup_cell_8,
    a.amount_of_pickups,
    a.avg_trip_cost
  FROM 
    aggregated_data a
  JOIN 
    cells_in_view v
  ON 
    a.pickup_cell_8 = v.h3_cell
);

In [0]:
print("::: PICKUP AGGREGATIONS @ H3 RESOLUTION 8")
visualize_with_kepler(
  dataframes=spark.sql("""
SELECT h3_h3tostring(pickup_cell_8) as pickup_cell_8, avg_trip_cost -- converting to string due to kepler limitation
FROM pickup_parent_cell_8_v 
"""), 
  wkt_viewport='POLYGON ((-74.050598 40.699381, -74.050598 40.793279, -73.848724 40.793279, -73.848724 40.699381, -74.050598 40.699381))',
  zoom_level=12.25,
  include_map_extent=True
)

::: PICKUP AGGREGATIONS @ H3 RESOLUTION 8
User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


<!doctype html> Kepler.gl

#### Can repeat for any / all H3 resolutions

> The blog discusses on-the-fly calcs for parent resolutions, e.g. using `h3_toparent(pickup_cell_12, 9)`.

## H3 Indexing System Tips

> If only the world were flat ... When using H3, you need to reason about hierarchy and how parent / child resolutions are rotated ~20 degrees. In the image below, points near cell edges may lead to over or under counting when moving “up” the H3 hierarchy to coarser resolutions, like from any outer green cell to its yellow parent cell.

__You can somewhat overcome this H3 hierarchy characteristic by standardizing to all even or all odd resolutions, e.g. 8, 10, 12, as the aligment will be the same.__

In [0]:
print("...execute this cell to see the image discussed ^")
displayHTML("""<img src='data:image/jpeg;base64, ...' width='50%'/>""")

...execute this cell to see the image discussed ^


> When exploring H3 cells on web maps, it’s useful to know the difference between spherical and flat-plane models.

1. __Spherical Model (Geography Type):__ H3 assumes a spherical Earth.
1. __Flat-Plane Model (Geometry Type):__ Projections like Web Mercator, common in web mapping, model Earth’s surface as a flat cartesian plane.
1. __Impact of Switching Representations:__ Transitioning from a spherical to a flat-plane model may introduce visual misalignments in cell boundaries but does not affect the geographic accuracy of point indexing.

__In the image below, curved cell edges from the spherical model are straightened on the flat plane; these are particularly noticeable at coarse resolutions.__

In [0]:
print("...executed this cell to see the image discussed ^")
displayHTML("""<img src='data:image/png;base64, ...' width='100%'/>""")

...executed this cell to see the image discussed ^


> See the final Notebook for how to convert this approach into a customizable, interactive app.